In [9]:
import numpy as np
import sys
import os
import xlwt
import xlrd
from xlutils.copy import copy

In [10]:
# networkx library helps in working with graphs ...
# and later performing the PageRank algorithm which is the crux of this implementation to find ...
# the importance of each sentence using their 'rank' as a metric rank
# the output of the method textrank, is a measure of importance of sentences
# this library has been used in the cell no. ()
import networkx as nx

In [11]:
# the PunktSentenceTokenizer library is being imported from the file punkt.py contained in package nltk.tokenize 
# this is used to tokenize the document into sentences
from nltk.tokenize.punkt import PunktSentenceTokenizer

In [12]:
# CountVectorizer: In this implementation, a CountVectorizer object is being created that ..
# will be used for creating the document-term matrix

# tFidTransformer: In this implementation,TfidfTransformer is used for executing the method fit_transform()... 
# which provides the output as a document-term matrix normalized (value 0-1) according to the TF-IDF
# TF(Term Frequency): the no. of times a term(a word here) appears in the current document(single sentence here)
# IDF(Inverse Document Frequency): the no. of times a term(a word here) appears in the entire corpus
# Corpus: set of all sentences

from sklearn.feature_extraction.text import TfidfTransformer, CountVectorizer

In [136]:
#read documents, return a string output containing the contents of the file. 
def readDoc(fileName):
    f = open(fileName, 'r',encoding='UTF-8')
    document = f.read()
    f.close()
    return document

#Output: A list containing sentences as its elements,sentences is a list containing each sentence of the document as an element  
def tokenize(fileName,document):
    file = open(fileName, 'r',encoding='UTF-8')
    filedata = file.readlines()
    title = ''
    count = 0
    firstSentence = []
    for eachLine in filedata:
        eachLine = eachLine[:-1]
        if len(eachLine) >= 1:
            if eachLine[:3] != 'URL' and eachLine[:2] != 'ID' and eachLine[:4] != 'Date' and eachLine[:8] != 'Ariticle':
                if eachLine[:5] == 'Title':
                    title += eachLine[8:]
                else: 
                    temp = eachLine.split(". ")
                    temp2 = temp[0].split(" ")
#                     print("temp",temp)
                    if len(temp2) > 5:
                        firstSentence += temp
#                         print("firstSentence",firstSentence)
                        break
    file.close()
    doc_tokenizer = PunktSentenceTokenizer()
    sentences_list = doc_tokenizer.tokenize(document)
#     print("sentence_list",sentences_list)
#     print("firstSentence",firstSentence)
    if len(sentences_list) == 1:
        return firstSentence,title
    elif firstSentence == sentences_list[1]:
        return sentences_list,title
    else:
#     print(firstSentence + sentences_list[1:])
        return firstSentence + sentences_list[1:],title

def summarize(fileName):
    document = readDoc(fileName)
    sentences_list,title = tokenize(fileName,document)
#     print("sentences_list",sentences_list)
    if len(sentences_list) != 0:
        #Generate term-document matrix(TD matrix) of the data
        # Convert a collection of text documents to a matrix of token counts
        # fit_transform method of CountVectorizer() class 
        # Learn the vocabulary dictionary and return term-document matrix. 
        # I/p: An iterable which yields either str, unicode or file objects.
        # O/p: The term-document matrix named cv_matrix
        cv = CountVectorizer()
        cv_matrix = cv.fit_transform(sentences_list)

        # Tnormalized: document-term matrix normalized (value 0-1) according to the TF-IDF
        normal_matrix = TfidfTransformer().fit_transform(cv_matrix)
        res_graph = normal_matrix * normal_matrix.T
        nx_graph = nx.from_scipy_sparse_matrix(res_graph)

        # Getting the rank of every sentence using textrank
        # ranks is a dictionary with key=node(sentences) and value=textrank (the rank of each of the sentences)
        ranks = nx.pagerank(nx_graph)

        #Finding important sentences and generating summary
        # O/p: sentence_array is the sorted(descending order w.r.t. score value) 2-d array of ranks[sentence] and sentence 
        # For example, if there are two sentences: S1 (with a score of S1 = s1) and S2 with score s2, with s2>s1
        # then sentence_array is [[s2, S2], [s1, S1]]
        sentence_array = sorted(((ranks[i], s) for i, s in enumerate(sentences_list)), reverse=True)
        sentence_array = np.asarray(sentence_array)

        # fmax is the largest score value(the score of first element)
        rank_max = float(sentence_array[0][0])
        rank_min = float(sentence_array[len(sentence_array) - 1][0])

        # Normalization of the scores so that it comes out in the range 0-1
        # fmax becomes 1, fmin becomes 0
        temp_array = []

        # if all sentences have equal ranks, take the first sentence
        flag = 0
        if rank_max - rank_min == 0:
            temp_array.append(0)
            flag = 1

        # If the sentence has different ranks
        if flag != 1:
            for i in range(0, len(sentence_array)):
                temp_array.append((float(sentence_array[i][0]) - rank_min) / (rank_max - rank_min))

        # Calculation of threshold:
        # We take the mean value of normalized scores
        # any sentence with the normalized score 0.2 more than the mean value is considered to be threshold
        threshold = (sum(temp_array) / len(temp_array)) + 0.2

        # Separate out the sentences that satiasfy the criteria of having a score above the threshold
        sentence_list = []
        if len(temp_array) > 1:
            for i in range(0, len(temp_array)):
                if temp_array[i] > threshold:
                        sentence_list.append(sentence_array[i][1])
        else:
            sentence_list.append(sentence_array[0][1])

        summary = " ".join(str(x) for x in sentence_list)
        if len(sentence_list) < 3:
            summary = title +". "+ summary
    else:
        summary = title
#     print(summary)
    return summary


In [137]:
#start

# directory = "../"
# os.chdir(directory) 
cwd = os.getcwd() 
print(cwd)
files = os.listdir(cwd)  
booklist = xlrd.open_workbook('PreprocessedNewsList.xls')
sheet = booklist.sheet_by_index(0)
fileNames = (sheet.col_values(0))
directory = "./CovidNewsContents"
os.chdir(directory) 
cwd = os.getcwd()  
print(cwd)
files = os.listdir(cwd)  


newWb = copy(booklist)
newWs = newWb.get_sheet(0);#取sheet表
count = 1
for eachFile in files:
    print(count,': ',eachFile)
    sumText = summarize(eachFile)
    print(count,': ',sumText)
#     if count > 2:
#         break
    newWs.write(fileNames.index(eachFile[:-4]),2,sumText)
    count += 1

directory = "../"
os.chdir(directory)  
cwd = os.getcwd()  
print(cwd)
newWb.save('TFIDFSum.xls')


# summarize("CNNH2020042900010.txt")


C:\Users\sunykorea\Desktop\519\Test_Summarization-Sentiment_Analyze\FinalProject
C:\Users\sunykorea\Desktop\519\Test_Summarization-Sentiment_Analyze\FinalProject\CovidNewsContents
1 :  AFRO2020050500001.txt
1 :  WHO welcomes every opportunity to collaborate with countries and researchers to develop new therapies and encourages such collaboration for the development of effective and safe therapies for Africa and the world. African governments through their Ministers of Health adopted a resolution urging Member States to produce evidence on the safety, efficacy and quality of traditional medicine at the Fiftieth Session of the WHO Regional Committee for Africa in 2000. WHO is working with research institutions to select traditional medicine products which can be investigated for clinical efficacy and safety for COVID-19 treatment. The use of products to treat COVID-19, which have not been robustly investigated can put people in danger, giving a false sense of security and distracting the

14 :  South Africa: With Evictions Amid COVID-19, Our Social Fabric Could Tear Apart. If we are to come out of this lockdown without the stain of another massacre on our national conscience, the government needs to take decisive action against the brutal forms of policing that are increasingly generating anger and turning people against the state.
15 :  ALFR2020042900016.txt
15 :  South Africa: COVID-19 - the Science, the Politics and Suspension of Rights. Either populations achieve immunity, or we achieve some sort of resistance to the disease. Either populations achieve immunity, or we achieve some sort of resistance to the disease.
16 :  ALFR2020042900017.txt
16 :  Africa Scrambles to Ramp Up COVID-19 Testing. Nkengasong noted then that while Egypt was still just ahead of South Africa with the most cases, followed by Algeria, Morocco and Cameroon, a different ranking emerged if one looked at infections relative to population. Between last Thursday, April 23 and the previous Thursday

32 :  On the countrywide scale, Kampala is rated with the lowest poverty rates of 0.7 per cent of the total population, and out of the poverty rate for the central region of 7.8 per cent. A 2016 World Bank Poverty Assessment Report for the period 2006 to 2013 described the country's poverty reduction as a remarkable story and detailed that the proportion of the Ugandan population living beneath the national poverty line declined from 31.1 per cent in 2006 to 19.7 per cent in 2013. "If agriculture is not affected, then the number of people sliding into poverty will not be high," Dr Guloba says, adding: "It is only those who depend on remittances from urban areas which have been hit by the crisis that we will see sliding into poverty, just like those in urban areas whose streams of incomes are linked to the outside world which is being affected." "In urban areas, the levels of informality of business is high, and that is where the most vulnerability to poverty is. Across the country, 19.

38 :  The economic and physical disruptions caused by the disease could have vast consequences for the rights and health of women and girls, a new analysis by UNFPA and partners shows. The economic and physical disruptions caused by the disease could have vast consequences for the rights and health of women and girls, a new analysis by UNFPA and partners shows. The pandemic is also expected to cause significant delays in programmes to end female genital mutilation and child marriage, resulting in an estimated 2 million more cases of FGM over the next decade than would otherwise have occurred. Millions of girls at risk
FGM and child marriage are also projected to increase, in large part due to delays in the implementation of programmes to end these harmful practices. And because poverty is a known driver of child marriage - with families more likely to marry off daughters in times of economic stress to alleviate the perceived burden of caring for them - the anticipated economic fallout 

48 :  Nigeria: 20 Doctors Tested Positive for COVID-19, Says NMA. "Information available to the Nigerian Medical Association reveals that a total number of 264 doctors have been exposed to COVID-19 situations out of which 20 actually contracted the infection, 2 have recovered so far with three mortalities. Francis Faduyile, the association said the doctors were among the over 66 healthcare workers who had tested positive after their exposure.
49 :  ALFR2020042900051.txt
49 :  Nigeria's COVID-19 Cases Surge By 195 to 1,532. The number represents the highest so far recorded in a single day since the outbreak started in Nigeria February 27. Nigeria has recorded 195 new cases of COVID-19, bringing to 1532 the total number of confirmed cases in the country.
50 :  ALFR2020042900052.txt
50 :  The Secretary to the Government of the Federation and chairman of the Presidential Task Force on COVID-19, Boss Mustapha, says the next phase for the country in the fight against COVID-19 is a very serio

...

Moscow, the country's worst-hit region, confirmed 5,795 new cases in the period, bringing its total to 74,401. MOSCOW, May 4 (Xinhua) -- Russia has reported 10,581 new confirmed COVID-19 cases over the past 24 hours, with the total number of infections rising to 145,268 as of Monday, the country's coronavirus response center said in a statement. Moscow, the country's worst-hit region, confirmed 5,795 new cases in the period, bringing its total to 74,401.
6071 :  XINH2020050400065.txt
6071 :  politicians' actions are "a smokescreen designed ... to keep the American people in a fog, to distort the truth, and to always deny accountability or responsibility for themselves," said a former member of the Iowa House of Representatives. politicians' actions are "a smokescreen designed ... to keep the American people in a fog, to distort the truth, and to always deny accountability or responsibility for themselves." The allegation that China should compensate is extremely absurd, he said, noting

6085 :  (Photo by Michael Nagle/Xinhua)
The models forecast about 200,000 new cases each day by the end of the month, up from about 25,000 cases now, according to a report published by The New York Times. model projects about 3,000 daily deaths by early June: media
Ariticle : 
A New York City urban park ranger hands out free face masks at the Prospect Park in the Brooklyn borough of New York, the United States, May 3, 2020. The projections, based on government modeling pulled together in chart form by the Federal Emergency Management Agency, forecast about 200,000 new cases each day by the end of the month, up from about 25,000 cases now, according to the report.
6086 :  XINH2020050500009.txt
6086 :  The Egyptian health ministry confirmed on Monday 348 new cases of COVID-19, bringing the total number in the country to 6,813. The Omani Ministry of Health announced 69 new confirmed cases of COVID-19, bringing the total number of cases in the country to 2,637. (Xinhua/Ahmed Gomaa)
The Ira

6104 :  Zhao and her husband removed the yolk from eggs and allowed the kids to try finger painting on the shells. For a start, she drills a hole on the bottom of the egg to drain the contents inside, and leaves it to dry in the shade, as the sun will make it too brittle for painting. "Although I cannot go to the frontline and save lives, I can tell the heroic stories through drawing and inspire more people to defeat the coronavirus," said Zhao, a Beijing-based folk artist. "I can tell the heroic stories through drawing and inspire more people to defeat the coronavirus," said Zhao. Zhao's painted and carved eggshells cover a wide range of themes, such as the Chinese Lunar New Year, figures from the classics and the 2008 Beijing Olympic Games.
6105 :  XINH2020050500037.txt
6105 :  Europe sees continued slowdown in new COVID-19 cases. Xinhua correspondent Zhang Yuan brings you the latest.
6106 :  XINH2020050500038.txt
6106 :  (Xinhua/Javed Dar)
-- India reports 3,597 new COVID-19 cases, 

6119 :  Israeli PM announces ease of COVID-19 rules. Prime Minister Benjamin Netanyahu announced on Monday a relaxation of additional COVID-19 restrictions in Israel.He hailed the anti-virus progress showed by a declining number of new infections and an increasing number of recoveries.The new rules cancels the 100-0meter-from-home restriction and allow visits by first-degree relatives and gatherings of up to 20 people
6120 :  XINH2020050500058.txt
6120 :  (Xinhua)
President Cyril Ramaphosa defends the government's decision to extend a ban on tobacco sale that had been put in place as part of a nationwide lockdown in March. CAPE TOWN, May 5 (Xinhua) -- President Cyril Ramaphosa said on Monday that the government's decision to extend a ban on tobacco sale was based on "careful consideration and discussion." He was responding to growing public complaints on the government's decision to extend the prohibition on the sale of tobacco products as the country moved from level five restrictions

6135 :  But in much of Europe, people wearing face masks were often met with strange looks in the early days of the coronavirus pandemic. BRUSSELS, May 5 (Xinhua) -- Wearing masks, keeping distance, working and schooling on staggered times, Europeans are restarting their "normal" life -- but in an unfamiliar way after a nearly two-month lockdown to fight the coronavirus. Portugal, where easing of nearly 50-day lockdown also started on Monday, the government even sent security forces to public transport stations to monitor the mask-wearing of passengers. (Photo by Kevin Voigt/Xinhua)
UNFAMILIAR "NORMAL" LIFE
After closing for seven weeks due to the COVID-19, Austrian schools reopened to graduating classes on Monday, with teachers and students trying to adapt to the new routine of wearing masks, washing hands frequently and keeping social distance. One of the first measures announced by Belgian Prime Minister Sophie Wilmes after the country began its first phase of deconfinement on Monda